In [509]:
import geopandas as gpd
import pandas as pd
import numpy as np
from shapely.geometry import Point
import osmnx as ox

In [510]:
CMA_SHP_PATH = r"/data/CMA_boundary_file/lcma000b21a_e.shp"

cma = gpd.read_file(CMA_SHP_PATH)
cma = cma.to_crs("EPSG:4326")  # OSM uses WGS84

print("CRS:", cma.crs)
print("Columns:", list(cma.columns))
print("Rows:", len(cma))

CRS: EPSG:4326
Columns: ['CMAUID', 'CMAPUID', 'DGUID', 'DGUIDP', 'CMANAME', 'CMATYPE', 'LANDAREA', 'PRUID', 'geometry']
Rows: 156


In [511]:
# Find the correct “name” column and select Toronto
for col in cma.columns:
    if cma[col].dtype == "object":
        uniques = cma[col].dropna().astype(str).unique()[:10]
        print(col, "sample uniques:", uniques)

CMAUID sample uniques: ['001' '010' '011' '015' '105' '110' '205' '210' '215' '220']
CMAPUID sample uniques: ['10001' '10010' '10011' '10015' '11105' '11110' '12205' '12210' '12215'
 '12220']
DGUID sample uniques: ['2021S0503001' '2021S0504010' '2021S0504011' '2021S0504015'
 '2021S0504105' '2021S0504110' '2021S0503205' '2021S0504210'
 '2021S0504215' '2021S0504220']
DGUIDP sample uniques: ['2021S050613330' '2021S050624330' '2021S050624502' '2021S050635502'
 '2021S050524505' '2021S050535505' '2021S050647840' '2021S050648840']
CMANAME sample uniques: ["St. John's" 'Grand Falls-Windsor' 'Gander' 'Corner Brook'
 'Charlottetown' 'Summerside' 'Halifax' 'Kentville' 'Truro' 'New Glasgow']
CMATYPE sample uniques: ['B' 'D' 'K']
PRUID sample uniques: ['10' '11' '12' '13' '24' '35' '46' '47' '48' '59']


In [512]:
NAME_COL = "CMANAME" 

toronto_cma = cma[cma[NAME_COL].astype(str).str.contains("Toronto", case=False, na=False)].copy()

if len(toronto_cma) == 0:
    raise ValueError("No Toronto CMA row found. Check NAME_COL and spelling.")
elif len(toronto_cma) > 1:
    print("Multiple Toronto rows found. Using dissolved polygon of all matches.")
    toronto_poly = toronto_cma.unary_union
else:
    toronto_poly = toronto_cma.geometry.iloc[0]

toronto_poly

In [513]:
# Pull OSM bank branches inside Toronto CMA
ox.settings.use_cache = True
ox.settings.log_console = True

tags = {"amenity": ["bank"]}

osmf = ox.features_from_polygon(toronto_poly, tags)
osmf = gpd.GeoDataFrame(osmf, geometry="geometry", crs="EPSG:4326")

print("Raw OSM features:", len(osmf))
osmf.head(2)

Raw OSM features: 1241


geometry alt_name amenity  atm brand  \
element id                                                                 
node    42606800  POINT (-79.38779 43.65469)      NaN    bank  yes   RBC   
        48553584  POINT (-79.34514 43.67907)      NaN    bank  NaN   RBC   

                 brand:wikidata          brand:wikipedia  check_date  \
element id                                                             
node    42606800        Q735261  en:Royal Bank of Canada  2025-12-02   
        48553584        Q735261  en:Royal Bank of Canada         NaN   

                            name                              opening_hours  \
element id                                                                    
node    42606800  RBC Royal Bank  Mo-Th 09:30-17:00; Fr 09:30-18:00; PH off   
        48553584             RBC                                        NaN   

                  ... wikidata roof:material roof:shape source_1 loc_name  \
element id        ...                                                       
node    42606800  ...      NaN           NaN        NaN      NaN      NaN   
        48553584  ...      NaN           NaN        NaN      NaN      NaN   

                 smoking source:opening_hours room roof:colour designation  
element id                                                                  
node    42606800     NaN                  NaN  NaN         NaN         NaN  
        48553584     NaN                  NaN  NaN         NaN         NaN  

[2 rows x 104 columns]

In [514]:
# build dim_branch
# Convert polygons to centroids so everything is a point
osmf["geometry"] = osmf["geometry"].apply(lambda g: g.centroid if g.geom_type != "Point" else g)

keep_cols = [c for c in [
    "name", "operator", "brand",
    "addr:housenumber", "addr:street", "addr:city",
    "addr:province", "addr:postcode",
    "amenity"
] if c in osmf.columns]

dim_branch = osmf[keep_cols + ["geometry"]].copy().reset_index(drop=True)
dim_branch["lon"] = dim_branch.geometry.x
dim_branch["lat"] = dim_branch.geometry.y

# Bank name: prefer operator then brand
dim_branch["bank_name"] = dim_branch["operator"] if "operator" in dim_branch.columns else None
if "brand" in dim_branch.columns:
    dim_branch["bank_name"] = dim_branch["bank_name"].fillna(dim_branch["brand"])

# Branch name fallback
dim_branch["branch_name"] = dim_branch["name"] if "name" in dim_branch.columns else None
dim_branch["branch_name"] = dim_branch["branch_name"].fillna(dim_branch["bank_name"]).fillna("Bank Branch")

# Address
def build_address(row):
    parts = []
    if "addr:housenumber" in row and pd.notna(row["addr:housenumber"]): parts.append(str(row["addr:housenumber"]))
    if "addr:street" in row and pd.notna(row["addr:street"]): parts.append(str(row["addr:street"]))
    return " ".join(parts) if parts else None

dim_branch["address"] = dim_branch.apply(build_address, axis=1)
dim_branch["city"] = dim_branch["addr:city"] if "addr:city" in dim_branch.columns else None
dim_branch["postal_code"] = dim_branch["addr:postcode"] if "addr:postcode" in dim_branch.columns else None

dim_branch["branch_type"] = "branch"

# branch_id
dim_branch["branch_id"] = (
    dim_branch["bank_name"].fillna("Unknown").astype(str) + "|" +
    dim_branch["branch_name"].fillna("Branch").astype(str) + "|" +
    dim_branch["lat"].round(6).astype(str) + "|" +
    dim_branch["lon"].round(6).astype(str)
).apply(lambda s: "BR_" + str(abs(hash(s)))[:12])

# Synthetic head officials
rng = np.random.default_rng(42)
first_names = ["Alex","Sam","Taylor","Jordan","Casey","Morgan","Riley","Avery","Jamie","Drew"]
last_names  = ["Patel","Chen","Singh","Brown","Nguyen","Martin","Wilson","Khan","Lopez","Davis"]
dim_branch["head_official_name"] = [f"{rng.choice(first_names)} {rng.choice(last_names)}" for _ in range(len(dim_branch))]

dim_branch = gpd.GeoDataFrame(dim_branch, geometry="geometry", crs="EPSG:4326")

print("Clean branches:", len(dim_branch)) 
dim_branch.head(3)

Clean branches: 1241


name operator          brand addr:housenumber        addr:street  \
0  RBC Royal Bank      NaN            RBC              443  University Avenue   
1             RBC      NaN            RBC              NaN                NaN   
2   National Bank      NaN  National Bank              NaN                NaN   

  addr:city addr:province addr:postcode amenity                    geometry  \
0   Toronto           NaN       M5G 2H6    bank  POINT (-79.38779 43.65469)   
1       NaN           NaN           NaN    bank  POINT (-79.34514 43.67907)   
2       NaN           NaN           NaN    bank  POINT (-79.34547 43.67867)   

         lon        lat      bank_name     branch_name                address  \
0 -79.387788  43.654686            RBC  RBC Royal Bank  443 University Avenue   
1 -79.345137  43.679073            RBC             RBC                   None   
2 -79.345473  43.678672  National Bank   National Bank                   None   

      city postal_code branch_type        branch_id head_official_name  
0  Toronto     M5G 2H6      branch  BR_731295883515          Alex Khan  
1      NaN         NaN      branch  BR_489883923227       Riley Nguyen  
2      NaN         NaN      branch  BR_424929734798        Casey Lopez

In [515]:
# create branch_lookup (address/city/postal + lat/lon)
# Ensure these columns exist (some may be missing in OSM)
for col in ["address", "city", "postal_code"]:
    if col not in dim_branch.columns:
        dim_branch[col] = None

branch_lookup = dim_branch[[
    "branch_id", "branch_name", "bank_name",
    "lat", "lon",
    "address", "city", "postal_code"
]].drop_duplicates().copy()

# Standardize missing values
branch_lookup["address"] = branch_lookup["address"].fillna("Not available")
branch_lookup["city"] = branch_lookup["city"].fillna("Not available")
branch_lookup["postal_code"] = branch_lookup["postal_code"].fillna("Not available")

In [516]:
majors = [
    r"\bTD\b",
    r"\bRBC\b",
    r"\bScotiabank\b",
    r"\bBMO\b",
    r"\bCIBC\b",
    r"\bNational Bank\b"
]
pattern = "|".join(majors)
dim_branch_major = dim_branch[
    dim_branch["bank_name"].fillna("").str.contains(pattern, case=False, regex=True)
].copy()
print("Major-bank branches:", len(dim_branch_major))

Major-bank branches: 1079


In [517]:
# Create synthetic clients inside Toronto CMA
def random_points_in_polygon(polygon, n, seed=7):
    rng = np.random.default_rng(seed)
    minx, miny, maxx, maxy = polygon.bounds
    pts = []
    while len(pts) < n:
        x = rng.uniform(minx, maxx)
        y = rng.uniform(miny, maxy)
        p = Point(x, y)
        if polygon.contains(p):
            pts.append(p)
    return pts

N_CUSTOMERS = 5000  # adjust for speed
cust_points = random_points_in_polygon(toronto_poly, N_CUSTOMERS, seed=11)

cust = gpd.GeoDataFrame(
    {"cust_id": np.arange(1, N_CUSTOMERS + 1)},
    geometry=cust_points,
    crs="EPSG:4326"
)

rng = np.random.default_rng(99)
cust_first = ["Andrea","Chris","Taylor","Jordan","Ari","Cam","Dana","Emi","Leo","Noah","Sofia","Maya","Nina","Omar","Zoe"]
cust_last  = ["Johnson","Smith","Brown","Miller","Wilson","Garcia","Martinez","Lee","Wong","Kaur","Singh","Chen","Patel","Nguyen","Davis"]
cust["cust_name"] = [f"{rng.choice(cust_first)} {rng.choice(cust_last)}" for _ in range(len(clients))]

cust["home_lon"] = cust.geometry.x
cust["home_lat"] = cust.geometry.y
cust["cust_city"] = np.where(
    inside_city,
    "Toronto",
    "Outside Toronto"
)

today = pd.Timestamp.today().normalize()
start = today - pd.Timedelta(days=15*365)
cust["first_acct_open_dt"] = pd.to_datetime(
    rng.integers(
        start.value // 10**9,
        today.value // 10**9,
        size=len(cust)
    ),
    unit="s"
)
cust["tenure_days"] = (today - cust["first_acct_open_dt"]).dt.days

# Mobile banking probability (mildly correlated with lower tenure)
prob_mobile = np.clip(0.80 - (cust["tenure_days"]/(15*365))*0.25, 0.45, 0.90)
cust["uses_mobile_banking"] = rng.random(len(cust)) < prob_mobile

# Synthetic avg daily transaction count per customer
tenure_years = cust["tenure_days"] / 365.25
base = rng.lognormal(mean=-0.15, sigma=0.55, size=len(cust))  
mobile_boost = np.where(cust["uses_mobile_banking"], 1.20, 0.90)
tenure_boost = 1.0 + 0.03 * np.clip(tenure_years, 0, 15)   
wealth_proxy = np.clip(tenure_years / 15, 0, 1)  
wealth_penalty = 1.0 - 0.25 * wealth_proxy
avg_daily = base * mobile_boost * tenure_boost * wealth_penalty
avg_daily = avg_daily + rng.normal(0, 0.15, size=len(cust))
cust["avg_daily_txn_count"] = np.round(np.clip(avg_daily, 0.05, 25.0), 2)

cust.head(3)

cust_id                    geometry   cust_name   home_lon   home_lat  \
0        1   POINT (-80.0173 43.91497)     Zoe Lee -80.017298  43.914971   
1        2  POINT (-80.08715 43.51293)   Maya Wong -80.087150  43.512931   
2        3  POINT (-79.72849 43.92815)  Taylor Lee -79.728494  43.928149   

         cust_city  first_acct_open_dt  tenure_days  uses_mobile_banking  \
0  Outside Toronto 2023-10-01 09:12:12          833                 True   
1  Outside Toronto 2021-06-28 01:53:31         1658                 True   
2  Outside Toronto 2021-04-24 23:00:31         1723                 True   

   avg_daily_txn_count  
0                 1.15  
1                 1.90  
2                 1.12

In [518]:
cust[["first_acct_open_dt", "tenure_days"]].head()

first_acct_open_dt  tenure_days
0 2023-10-01 09:12:12          833
1 2021-06-28 01:53:31         1658
2 2021-04-24 23:00:31         1723
3 2018-02-28 02:49:42         2874
4 2020-07-09 04:09:19         2012

In [519]:
NEIGH_SHP_PATH = r"/data/Neighbourhoods/Neighbourhoods - 4326.shp"
neigh = gpd.read_file(NEIGH_SHP_PATH)
neigh["geometry"] = neigh.geometry.buffer(0)

print(neigh.crs)

EPSG:4326


In [520]:
print(neigh.columns)
neigh.head()

Index(['_id1', 'AREA_ID2', 'AREA_AT3', 'PARENT_4', 'AREA_SH5', 'AREA_LO6',
       'AREA_NA7', 'AREA_DE8', 'CLASSIF9', 'CLASSIF10', 'OBJECTI11',
       'geometry'],
      dtype='object')


_id1  AREA_ID2  AREA_AT3  PARENT_4 AREA_SH5 AREA_LO6  \
0     1   2502366  26022881       NaN      174      174   
1     2   2502365  26022880       NaN      173      173   
2     3   2502364  26022879       NaN      172      172   
3     4   2502363  26022878       NaN      171      171   
4     5   2502362  26022877       NaN      170      170   

                    AREA_NA7                         AREA_DE8  \
0  South Eglinton-Davisville  South Eglinton-Davisville (174)   
1              North Toronto              North Toronto (173)   
2         Dovercourt Village         Dovercourt Village (172)   
3   Junction-Wallace Emerson   Junction-Wallace Emerson (171)   
4         Yonge-Bay Corridor         Yonge-Bay Corridor (170)   

                               CLASSIF9 CLASSIF10   OBJECTI11  \
0  Not an NIA or Emerging Neighbourhood        NA  17824737.0   
1  Not an NIA or Emerging Neighbourhood        NA  17824753.0   
2  Not an NIA or Emerging Neighbourhood        NA  17824769.0   
3  Not an NIA or Emerging Neighbourhood        NA  17824785.0   
4  Not an NIA or Emerging Neighbourhood        NA  17824801.0   

                                            geometry  
0  POLYGON ((-79.38635 43.69783, -79.38623 43.697...  
1  POLYGON ((-79.39744 43.70693, -79.39837 43.706...  
2  POLYGON ((-79.43411 43.66015, -79.43537 43.659...  
3  POLYGON ((-79.4387 43.66766, -79.43841 43.6669...  
4  POLYGON ((-79.38404 43.64497, -79.38502 43.644...

In [521]:
print(cust.crs)
cust.head()

EPSG:4326


cust_id                    geometry   cust_name   home_lon   home_lat  \
0        1   POINT (-80.0173 43.91497)     Zoe Lee -80.017298  43.914971   
1        2  POINT (-80.08715 43.51293)   Maya Wong -80.087150  43.512931   
2        3  POINT (-79.72849 43.92815)  Taylor Lee -79.728494  43.928149   
3        4  POINT (-79.37551 43.67128)   Zoe Davis -79.375512  43.671280   
4        5  POINT (-79.36648 43.92923)    Zoe Kaur -79.366481  43.929229   

         cust_city  first_acct_open_dt  tenure_days  uses_mobile_banking  \
0  Outside Toronto 2023-10-01 09:12:12          833                 True   
1  Outside Toronto 2021-06-28 01:53:31         1658                 True   
2  Outside Toronto 2021-04-24 23:00:31         1723                 True   
3          Toronto 2018-02-28 02:49:42         2874                 True   
4  Outside Toronto 2020-07-09 04:09:19         2012                 True   

   avg_daily_txn_count  
0                 1.15  
1                 1.90  
2                 1.12  
3                 0.80  
4                 2.19

In [522]:
# spatial join
cust_neigh = gpd.sjoin(
    cust,
    neigh[["AREA_NA7", "geometry"]],
    how="left",
    predicate="intersects"
)

In [523]:
cust_neigh["cust_neighbourhood"] = cust_neigh["AREA_NA7"].str.title()

In [524]:
cust = cust_neigh.drop(columns=["index_right"])

In [525]:
cust["cust_neighbourhood"].value_counts().head(10)

cust_neighbourhood
Morningside Heights               21
West Humber-Clairville            16
Eringate-Centennial-West Deane    11
St.Andrew-Windfields              10
West Rouge                        10
Clairlea-Birchmount                9
Milliken                           9
Woburn North                       9
Cliffcrest                         9
Etobicoke City Centre              8
Name: count, dtype: int64

In [526]:
cust = cust.drop(columns=["AREA_NA7"], errors="ignore")

In [527]:
cust["cust_neighbourhood"].isna().mean()

np.float64(0.8992)

In [528]:
cust["cust_neighbourhood"] = cust["cust_neighbourhood"].fillna("Outside Toronto")

In [529]:
cust.head()

cust_id                    geometry   cust_name   home_lon   home_lat  \
0        1   POINT (-80.0173 43.91497)     Zoe Lee -80.017298  43.914971   
1        2  POINT (-80.08715 43.51293)   Maya Wong -80.087150  43.512931   
2        3  POINT (-79.72849 43.92815)  Taylor Lee -79.728494  43.928149   
3        4  POINT (-79.37551 43.67128)   Zoe Davis -79.375512  43.671280   
4        5  POINT (-79.36648 43.92923)    Zoe Kaur -79.366481  43.929229   

         cust_city  first_acct_open_dt  tenure_days  uses_mobile_banking  \
0  Outside Toronto 2023-10-01 09:12:12          833                 True   
1  Outside Toronto 2021-06-28 01:53:31         1658                 True   
2  Outside Toronto 2021-04-24 23:00:31         1723                 True   
3          Toronto 2018-02-28 02:49:42         2874                 True   
4  Outside Toronto 2020-07-09 04:09:19         2012                 True   

   avg_daily_txn_count   cust_neighbourhood  
0                 1.15      Outside Toronto  
1                 1.90      Outside Toronto  
2                 1.12      Outside Toronto  
3                 0.80  North St.James Town  
4                 2.19      Outside Toronto

In [530]:
# Create products (deposits + credit card flag)
rng = np.random.default_rng(123)

# 0) Customer-level: interest-bearing checking flag
tenure_years = cust["tenure_days"] / 365.25
wealth_proxy = np.clip(tenure_years / 15, 0, 1)

p_ib_checking = np.clip(
    0.18 + 0.22 * wealth_proxy + 0.10 * cust["uses_mobile_banking"].astype(int),
    0.10, 0.65
)

cust["has_interest_checking"] = rng.random(len(cust)) < p_ib_checking

# 1) Build product fact table
rows = []
deposit_universe = ["Checking", "Savings", "Money Market", "CD"]

for cid in cust["cust_id"].values:
    n_dep = int(rng.integers(1, 4))
    dep_products = rng.choice(deposit_universe, size=n_dep, replace=False)

    mobile = bool(cust.loc[cust.cust_id == cid, "uses_mobile_banking"].iloc[0])
    has_cc = rng.random() < (0.55 if mobile else 0.40)

    for pt in dep_products:
        if pt == "Checking":
            bal = float(np.round(np.exp(rng.normal(8.6, 0.9)), 2))
        elif pt == "Savings":
            bal = float(np.round(np.exp(rng.normal(9.0, 1.0)), 2))
        elif pt == "Money Market":
            bal = float(np.round(np.exp(rng.normal(9.4, 1.0)), 2))
        elif pt == "CD":
            bal = float(np.round(np.exp(rng.normal(9.8, 1.1)), 2))
        rows.append((cid, pt, bal, "Y"))

    rows.append((cid, "Credit Card", 0.0, "Y" if has_cc else "N"))

fact_cust_product = pd.DataFrame(
    rows, columns=["cust_id", "product_type", "balance", "active_flag"]
)

In [531]:
# Product presence flags + balances (wide customer table)
active = fact_cust_product.query("active_flag == 'Y'").copy()

deposit_wide = (active
    .query("product_type != 'Credit Card'")
    .pivot_table(
        index="cust_id",
        columns="product_type",
        values="balance",
        aggfunc="sum",
        fill_value=0.0
    )
    .reset_index()
)

deposit_wide = deposit_wide.rename(columns={
    "Checking": "checking_balance",
    "Savings": "savings_balance",
    "Money Market": "money_market_balance",
    "CD": "cd_balance"
})

# Ensure missing columns exist
for col in ["checking_balance", "savings_balance", "money_market_balance", "cd_balance"]:
    if col not in deposit_wide.columns:
        deposit_wide[col] = 0.0

# Presence flags (derived)
deposit_wide["has_checking"] = deposit_wide["checking_balance"] > 0
deposit_wide["has_savings"] = deposit_wide["savings_balance"] > 0
deposit_wide["has_money_market"] = deposit_wide["money_market_balance"] > 0
deposit_wide["has_cd"] = deposit_wide["cd_balance"] > 0

In [532]:
# Align to NIDDA vs IBB
fact = fact_cust_product.merge(
    cust[["cust_id", "has_interest_checking"]],
    on="cust_id",
    how="left"
)

def categorize(row):
    pt = row["product_type"]
    if pt == "Checking":
        return "IBB" if bool(row["has_interest_checking"]) else "NIDDA"
    if pt in ["Savings", "Money Market", "CD"]:
        return "IBB"
    return None

fact["deposit_category"] = fact.apply(categorize, axis=1)

dep_active = fact.query("active_flag == 'Y' and deposit_category.notnull()").copy()

nidda_ibb = (dep_active
    .groupby(["cust_id", "deposit_category"], as_index=False)["balance"]
    .sum()
    .pivot(index="cust_id", columns="deposit_category", values="balance")
    .fillna(0.0)
    .reset_index()
)

if "NIDDA" not in nidda_ibb.columns:
    nidda_ibb["NIDDA"] = 0.0
if "IBB" not in nidda_ibb.columns:
    nidda_ibb["IBB"] = 0.0

nidda_ibb = nidda_ibb.rename(columns={"NIDDA": "nidda_balance", "IBB": "ibb_balance"})
nidda_ibb["total_deposit_balance"] = (
    nidda_ibb["nidda_balance"] + nidda_ibb["ibb_balance"]
).round(2)

nidda_ibb["nidda_pct"] = np.round(
    nidda_ibb["nidda_balance"] / nidda_ibb["total_deposit_balance"].replace(0, np.nan),
    3
)

In [533]:
# Credit card flag + total products
credit_flag = (fact_cust_product
    .query("product_type == 'Credit Card'")
    .assign(has_credit_card=lambda d: d["active_flag"].eq("Y"))
    [["cust_id", "has_credit_card"]]
)

total_products = (active
    .groupby("cust_id", as_index=False)
    .size()
    .rename(columns={"size": "total_products"})
)

In [534]:
# Final customer product features table
cust_products = (deposit_wide
    .merge(nidda_ibb, on="cust_id", how="left")
    .merge(credit_flag, on="cust_id", how="left")
    .merge(total_products, on="cust_id", how="left")
)

cust_products["has_credit_card"] = cust_products["has_credit_card"].fillna(False)
cust_products["total_products"] = cust_products["total_products"].fillna(0).astype(int)

cust_products.head(3)

cust_id  cd_balance  checking_balance  money_market_balance  \
0        1     3473.51               0.0              17524.89   
1        2    20906.07               0.0               4970.66   
2        3        0.00               0.0                  0.00   

   savings_balance  has_checking  has_savings  has_money_market  has_cd  \
0          2850.31         False         True              True    True   
1          5637.00         False         True              True    True   
2          3857.52         False         True             False   False   

   ibb_balance  nidda_balance  total_deposit_balance  nidda_pct  \
0     23848.71            0.0               23848.71        0.0   
1     31513.73            0.0               31513.73        0.0   
2      3857.52            0.0                3857.52        0.0   

   has_credit_card  total_products  
0             True               4  
1            False               3  
2             True               2

In [535]:
# Top 3 closest branches + miles & minutes
branches_use = dim_branch_major

branches_proj = branches_use.to_crs("EPSG:26917")  # UTM 17N good for Toronto
cust_proj = cust.to_crs("EPSG:26917")

bx = branches_proj.geometry.x.values
by = branches_proj.geometry.y.values
branch_xy = np.vstack([bx, by]).T

cx = cust_proj.geometry.x.values
cy = cust_proj.geometry.y.values
cust_xy = np.vstack([cx, cy]).T

# Find top 3 nearest
try:
    from scipy.spatial import cKDTree
    tree = cKDTree(branch_xy)
    dist_m, idx = tree.query(cust_xy, k=3)
except Exception:
    from sklearn.neighbors import NearestNeighbors
    nn = NearestNeighbors(n_neighbors=3, algorithm="kd_tree")
    nn.fit(branch_xy)
    dist_m, idx = nn.kneighbors(cust_xy)

branch_ids = branches_proj["branch_id"].values
branch_names = branches_proj["branch_name"].values

top3 = pd.DataFrame({"cust_id": clients["cust_id"].values})

avg_mph = 25  # travel time estimate
for k in [1, 2, 3]:
    top3[f"top{k}_branch_id"] = branch_ids[idx[:, k-1]]
    top3[f"top{k}_branch_name"] = branch_names[idx[:, k-1]]

    miles = dist_m[:, k-1] / 1609.344
    top3[f"top{k}_miles"] = np.round(miles, 2)

    minutes = (miles / avg_mph) * 60
    top3[f"top{k}_minutes"] = np.round(minutes, 0).astype(int)

# One lookup for coords + address fields (from SAME branches_use)
branch_lookup = branches_use[[
    "branch_id", "lat", "lon", "address", "city", "postal_code"
]].drop_duplicates().copy()

for c in ["address", "city", "postal_code"]:
    branch_lookup[c] = branch_lookup[c].fillna("Not available")

# Merge lookup onto top1/top2/top3
for k in [1, 2, 3]:
    top3 = (top3
        .merge(branch_lookup, left_on=f"top{k}_branch_id", right_on="branch_id", how="left")
        .rename(columns={
            "lat": f"top{k}_lat",
            "lon": f"top{k}_lon",
            "address": f"top{k}_address",
            "city": f"top{k}_city",
            "postal_code": f"top{k}_postal_code",
        })
        .drop(columns=["branch_id"])
    )

In [536]:
# Build branch manager roster: 1 per branch (prefer Branch Manager, fallback Assistant Branch Manager)
mgr_pref = ["Branch Manager", "Assistant Branch Manager"]

mgr_pool = dim_employee[dim_employee["employee_title"].isin(mgr_pref)].copy()
mgr_pool["title_rank"] = mgr_pool["employee_title"].map({
    "Branch Manager": 1,
    "Assistant Branch Manager": 2
}).fillna(99)

mgr_pool = mgr_pool.sort_values(["branch_id", "title_rank", "employee_id"])

branch_manager = (
    mgr_pool.groupby("branch_id", as_index=False)
            .first()
            .rename(columns={
                "branch_id": "mgr_branch_id",
                "employee_id": "branch_manager_id",
                "employee_name": "branch_manager_name",
                "employee_title": "branch_manager_title"
            })
            [["mgr_branch_id", "branch_manager_id", "branch_manager_name", "branch_manager_title"]]
)

# Fallback for branches with no BM/ABM: pick any employee in that branch
missing_mgr = set(branches_use["branch_id"]) - set(branch_manager["mgr_branch_id"])
if missing_mgr:
    fallback = (dim_employee[dim_employee["branch_id"].isin(missing_mgr)]
                .sort_values(["branch_id", "employee_id"])
                .groupby("branch_id", as_index=False)
                .first()
                .rename(columns={
                    "branch_id": "mgr_branch_id",
                    "employee_id": "branch_manager_id",
                    "employee_name": "branch_manager_name",
                    "employee_title": "branch_manager_title"
                })
                [["mgr_branch_id", "branch_manager_id", "branch_manager_name", "branch_manager_title"]]
               )
    branch_manager = pd.concat([branch_manager, fallback], ignore_index=True)

# Merge manager roster onto top1/top2/top3
for k in [1, 2, 3]:
    top3 = (top3
        .merge(branch_manager, left_on=f"top{k}_branch_id", right_on="mgr_branch_id", how="left")
        .rename(columns={
            "branch_manager_id": f"top{k}_manager_id",
            "branch_manager_name": f"top{k}_manager_name",
            "branch_manager_title": f"top{k}_manager_title",
        })
        .drop(columns=["mgr_branch_id"])
    )

# Sanity check: should be ~0
print("Missing top1 coords rate:", top3["top1_lat"].isna().mean())
print("Missing top1 manager rate:", top3["top1_manager_id"].isna().mean())

top3.head(3)

Missing top1 coords rate: 0.0
Missing top1 manager rate: 0.0126


cust_id   top1_branch_id top1_branch_name  top1_miles  top1_minutes  \
0        1  BR_740698449815               TD        3.88             9   
1        2  BR_602463860093       Scotiabank        5.50            13   
2        3  BR_342389789867             CIBC        3.38             8   

    top2_branch_id top2_branch_name  top2_miles  top2_minutes  \
0  BR_105008083406              RBC        3.91             9   
1  BR_529658687004       Scotiabank        8.46            20   
2  BR_103892364959       Scotiabank        3.87             9   

    top3_branch_id  ... top3_postal_code  top1_manager_id  top1_manager_name  \
0  BR_879786875131  ...    Not available       EMP_101940       Casey Wilson   
1  BR_116087680036  ...          L7J 1H1       EMP_102631      Taylor Martin   
2  BR_490141147567  ...    Not available       EMP_102891        Jamie Lopez   

   top1_manager_title  top2_manager_id top2_manager_name  \
0      Branch Manager       EMP_100841     Morgan Martin   
1   Financial Advisor       EMP_101901      Jordan Davis   
2   Financial Advisor       EMP_103631        Drew Lopez   

         top2_manager_title top3_manager_id  top3_manager_name  \
0         Financial Advisor      EMP_101934         Casey Khan   
1      Relationship Manager      EMP_101906           Sam Chen   
2  Personal Banking Advisor      EMP_104854        Avery Patel   

         top3_manager_title  
0  Assistant Branch Manager  
1            Branch Manager  
2            Branch Manager  

[3 rows x 37 columns]

In [537]:
# Build a “current branch candidate pool” (non-top3 but plausible)
ID_COL = "cust_id" 

rng = np.random.default_rng(777)

# Must sum to 1.0
RATE_NEAREST = 0.70
RATE_TOP3 = 0.20
RATE_NON_TOP3 = 0.10
assert abs((RATE_NEAREST + RATE_TOP3 + RATE_NON_TOP3) - 1.0) < 1e-9

# Start from top1
primary_branch = top3[[ID_COL, "top1_branch_id", "top2_branch_id", "top3_branch_id"]].copy()
primary_branch["primary_branch_id"] = primary_branch["top1_branch_id"]

u = rng.random(len(primary_branch))

# Choose among top3 (biased)
mask_top3 = (u >= RATE_NEAREST) & (u < RATE_NEAREST + RATE_TOP3)
choices = rng.choice([1, 2, 3], size=mask_top3.sum(), p=[0.55, 0.30, 0.15])

top3_pick = np.where(
    choices == 1, primary_branch.loc[mask_top3, "top1_branch_id"].values,
    np.where(
        choices == 2, primary_branch.loc[mask_top3, "top2_branch_id"].values,
        primary_branch.loc[mask_top3, "top3_branch_id"].values
    )
)
primary_branch.loc[mask_top3, "primary_branch_id"] = top3_pick

# Choose outside top3 but still nearby (from ranks 4..K)
mask_non_top3 = (u >= RATE_NEAREST + RATE_TOP3)

# K must match how you built nearestK_branch_ids
K = nearestK_branch_ids.shape[1]
rank_candidates = np.arange(3, K)  # 0-based ranks; 3 = 4th nearest

weights = np.exp(-0.35 * (rank_candidates - 3))  # closer ranks higher weight
weights = weights / weights.sum()

picked_ranks = rng.choice(rank_candidates, size=mask_non_top3.sum(), p=weights)
cust_idx = np.where(mask_non_top3)[0]

primary_branch.loc[mask_non_top3, "primary_branch_id"] = nearestK_branch_ids[cust_idx, picked_ranks]

# Flag whether current branch is in top3
primary_branch = primary_branch[[ID_COL, "primary_branch_id", "top1_branch_id", "top2_branch_id", "top3_branch_id"]].copy()

primary_branch["primary_branch_in_top3"] = (
    (primary_branch["primary_branch_id"] == primary_branch["top1_branch_id"]) |
    (primary_branch["primary_branch_id"] == primary_branch["top2_branch_id"]) |
    (primary_branch["primary_branch_id"] == primary_branch["top3_branch_id"])
)

print("Pct primary branch outside top3:", (~primary_branch["primary_branch_in_top3"]).mean())

# Drop top columns so we DON'T create collisions later
primary_branch = primary_branch[[ID_COL, "primary_branch_id", "primary_branch_in_top3"]].copy()

Pct primary branch outside top3: 0.0862


In [538]:
branch_lookup = branches_use[[
    "branch_id", "branch_name",
    "lat", "lon",
    "address", "city", "postal_code"
]].drop_duplicates().copy()

for c in ["address", "city", "postal_code"]:
    branch_lookup[c] = branch_lookup[c].fillna("Not available")

# Project to meters for distance calculations
cust_proj = cust[[ID_COL, "geometry"]].to_crs("EPSG:26917").copy()
branches_proj = branches_use[["branch_id", "geometry"]].to_crs("EPSG:26917").copy()

cust_proj["cust_x"] = cust_proj.geometry.x
cust_proj["cust_y"] = cust_proj.geometry.y
cust_proj = cust_proj.drop(columns=["geometry"])

branches_proj["branch_x"] = branches_proj.geometry.x
branches_proj["branch_y"] = branches_proj.geometry.y
branches_proj = branches_proj.drop(columns=["geometry"]).drop_duplicates(subset=["branch_id"])

# Enrich current branch
primary_branch_enriched = (
    primary_branch
    .merge(branch_lookup, left_on="primary_branch_id", right_on="branch_id", how="left")
    .rename(columns={
        "branch_name": "primary_branch_name",
        "lat": "primary_branch_lat",
        "lon": "primary_branch_lon",
        "address": "primary_branch_address",
        "city": "primary_branch_city",
        "postal_code": "primary_branch_postal_code"
    })
    .drop(columns=["branch_id"])
    .merge(branches_proj, left_on="primary_branch_id", right_on="branch_id", how="left")
    .drop(columns=["branch_id"])
    .merge(cust_proj, on=ID_COL, how="left")
)

dx = primary_branch_enriched["cust_x"] - primary_branch_enriched["branch_x"]
dy = primary_branch_enriched["cust_y"] - primary_branch_enriched["branch_y"]

primary_branch_enriched["primary_branch_miles"] = np.round(np.sqrt(dx*dx + dy*dy) / 1609.344, 2)

avg_mph = 25
primary_branch_enriched["primary_branch_minutes"] = np.round(
    (primary_branch_enriched["primary_branch_miles"] / avg_mph) * 60, 0
).astype("Int64")

primary_branch_enriched = primary_branch_enriched[[
    ID_COL,
    "primary_branch_id",
    "primary_branch_name",
    "primary_branch_address",
    "primary_branch_city",
    "primary_branch_postal_code",
    "primary_branch_lat",
    "primary_branch_lon",
    "primary_branch_miles",
    "primary_branch_minutes",
    "primary_branch_in_top3",
]]

In [539]:
def pick_employee(group, cust_balance):
    if cust_balance >= 250_000:
        pref = ["Relationship Manager", "Senior Financial Advisor"]
    elif cust_balance >= 50_000:
        pref = ["Financial Advisor", "Senior Financial Advisor"]
    else:
        pref = ["Personal Banking Advisor"]

    filtered = group[group["employee_title"].isin(pref)]
    return filtered.sample(1, random_state=42) if not filtered.empty else group.sample(1, random_state=42)


EMP_PER_BRANCH = 5
rng = np.random.default_rng(202)

titles = [
    "Personal Banking Advisor",
    "Financial Advisor",
    "Senior Financial Advisor",
    "Relationship Manager",
    "Assistant Branch Manager",
    "Branch Manager"
]
title_weights = [0.35, 0.30, 0.15, 0.10, 0.05, 0.05]

emp_rows = []
emp_id = 100000
for bid in branches_use["branch_id"].values:
    for _ in range(EMP_PER_BRANCH):
        emp_id += 1
        emp_rows.append({
            "employee_id": f"EMP_{emp_id}",
            "employee_name": f"{rng.choice(first_names)} {rng.choice(last_names)}",
            "employee_title": rng.choice(titles, p=title_weights),
            "branch_id": bid
        })

dim_employee = pd.DataFrame(emp_rows)

# Join clients to employees of their current branch + bring in deposit balance for routing
tmp = (
    primary_branch
    .merge(dim_employee, left_on="primary_branch_id", right_on="branch_id", how="left")
    .merge(deposit_summary, on="cust_id", how="left")  # needs total_deposit_balance
)

tmp["total_deposit_balance"] = tmp["total_deposit_balance"].fillna(0.0)

# Pick the "most recent employee" based on client value
cust_employee = (
    tmp.groupby("cust_id", as_index=False)
       .apply(lambda g: pick_employee(g, g["total_deposit_balance"].iloc[0]))
       .reset_index(drop=True)
)

cust_employee = cust_employee[[
    "cust_id", "employee_id", "employee_name", "employee_title"
]].copy()

cust_employee.head(3)

/var/folders/mv/5grglnm12qj9pj0l3s5k20_40000gn/T/ipykernel_98904/4070490789.py:52: FutureWarning: DataFrameGroupBy.apply operated on the grouping columns. This behavior is deprecated, and in a future version of pandas the grouping columns will be excluded from the operation. Either pass `include_groups=False` to exclude the groupings or explicitly select the grouping columns after groupby to silence this warning.
  .apply(lambda g: pick_employee(g, g["total_deposit_balance"].iloc[0]))


cust_id employee_id employee_name            employee_title
0        1  EMP_101937  Riley Martin  Personal Banking Advisor
1        2  EMP_102635   Jamie Lopez  Personal Banking Advisor
2        3  EMP_102893  Morgan Brown  Personal Banking Advisor

In [540]:
final = (cust[[
            "cust_id", "cust_name", "first_acct_open_dt",
            "tenure_days", "uses_mobile_banking", "avg_daily_txn_count", "cust_city", "cust_neighbourhood"
        ]]
        .merge(cust_products, on="cust_id", how="left")   
        .merge(cust_employee, on="cust_id", how="left")
        .merge(top3, on="cust_id", how="left")
        .merge(primary_branch_enriched, on="cust_id", how="left")
)

# Clean nulls/types
final["total_products"] = final["total_products"].fillna(0).astype(int)
final["total_deposit_balance"] = final["total_deposit_balance"].fillna(0.0).round(2)
final["has_credit_card"] = final["has_credit_card"].fillna(False)

for c in ["has_checking", "has_savings", "has_money_market", "has_cd"]:
    final[c] = final[c].fillna(False)

for c in ["checking_balance", "savings_balance", "money_market_balance", "cd_balance",
          "nidda_balance", "ibb_balance"]:
    if c in final.columns:
        final[c] = final[c].fillna(0.0).round(2)

if "nidda_pct" in final.columns:
    final["nidda_pct"] = final["nidda_pct"].fillna(0.0)

final["primary_branch_minutes"] = final["primary_branch_minutes"].astype("Int64")

# Reorder columns (added product flags + NIDDA/IBB fields)
cols = [
    "cust_name", "cust_id",
    "employee_name", "employee_id", "employee_title",
    "first_acct_open_dt", "tenure_days", "cust_city", "cust_neighbourhood",

    # Relationship / products
    "total_products", "uses_mobile_banking",
    "total_deposit_balance", "nidda_balance", "ibb_balance", "nidda_pct",
    "has_checking", "has_savings", "has_money_market", "has_cd", "has_credit_card",
    "checking_balance", "savings_balance", "money_market_balance", "cd_balance",

    "avg_daily_txn_count",

    # Primary (current) branch
    "primary_branch_name", "primary_branch_id",
    "primary_branch_address", "primary_branch_city", "primary_branch_postal_code",
    "primary_branch_lat", "primary_branch_lon",
    "primary_branch_miles", "primary_branch_minutes",
    "primary_branch_in_top3",

    # Top 1
    "top1_branch_name", "top1_branch_id",
    "top1_lat", "top1_lon",
    "top1_address", "top1_city", "top1_postal_code",
    "top1_miles", "top1_minutes",
    "top1_manager_name", "top1_manager_id", "top1_manager_title",

    # Top 2
    "top2_branch_name", "top2_branch_id",
    "top2_lat", "top2_lon",
    "top2_address", "top2_city", "top2_postal_code",
    "top2_miles", "top2_minutes",
    "top2_manager_name", "top2_manager_id", "top2_manager_title",

    # Top 3
    "top3_branch_name", "top3_branch_id",
    "top3_lat", "top3_lon",
    "top3_address", "top3_city", "top3_postal_code",
    "top3_miles", "top3_minutes",
    "top3_manager_name", "top3_manager_id", "top3_manager_title",
]

# Safety: only keep columns that exist
missing = [c for c in cols if c not in final.columns]
if missing:
    raise KeyError(f"Missing columns in final before reordering: {missing}")

final = final[cols]

final.head(3)

cust_name  cust_id employee_name employee_id            employee_title  \
0     Zoe Lee        1  Riley Martin  EMP_101937  Personal Banking Advisor   
1   Maya Wong        2   Jamie Lopez  EMP_102635  Personal Banking Advisor   
2  Taylor Lee        3  Morgan Brown  EMP_102893  Personal Banking Advisor   

   first_acct_open_dt  tenure_days        cust_city cust_neighbourhood  \
0 2023-10-01 09:12:12          833  Outside Toronto    Outside Toronto   
1 2021-06-28 01:53:31         1658  Outside Toronto    Outside Toronto   
2 2021-04-24 23:00:31         1723  Outside Toronto    Outside Toronto   

   total_products  ...   top3_lat   top3_lon         top3_address  \
0               4  ...  43.919398 -80.097702        Not available   
1               3  ...  43.630712 -80.040553  31 Mill Street East   
2               2  ...  43.871465 -79.726150        Not available   

       top3_city  top3_postal_code  top3_miles  top3_minutes  \
0  Not available     Not available        4.02            10   
1  Not available           L7J 1H1        8.46            20   
2  Not available     Not available        3.91             9   

   top3_manager_name  top3_manager_id        top3_manager_title  
0         Casey Khan       EMP_101934  Assistant Branch Manager  
1           Sam Chen       EMP_101906            Branch Manager  
2        Avery Patel       EMP_104854            Branch Manager  

[3 rows x 71 columns]

In [541]:
final.to_csv("/data/cust_branch_dataset CLEANED.csv", index=False)